Imports and Time Management  
Creation of the Datasets (in each Dataset seperate!)  
Displaying the Widgets

#Initialization: Imports & Time Management

In [1]:
import sys
import site

# Add the user site-packages directory to the Python path
site.addsitedir('/tf/.local/lib/python3.11/site-packages')

import time
startTime = time.time()

import lorem
import tiktoken

from keras.datasets import mnist
from keras.utils import to_categorical

import colorsys
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import numpy as np
import random

import torch
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torch import nn
import torch.optim as optim
import torch.nn.functional as F
from torch.utils.data import Subset

import os
import json
import requests
import tensorflow as tf
from tqdm import tqdm

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print(device)

import plotly.graph_objects as go
import plotly.io as pio
pio.renderers.default = 'colab'

2024-05-25 15:57:52.109109: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-05-25 15:57:52.141117: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-25 15:57:52.141151: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-25 15:57:52.141167: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-05-25 15:57:52.148181: I tensorflow/core/platform/cpu_feature_g

cpu


In [2]:
#!git clone "https://github.com/luca-g97/Interactive-AI-Playground.git"

#!mv /content/Interactive-AI-Playground/* /content/
#!rm -rf /content/Interactive-AI-Playground/
#!rm /content/README.md

In [3]:
#import Images_HSVRGB as HSVRGB
#import Images_MNIST as MNIST
#import LLM_Small1x1 as Small1x1

#Initialization: Datasets

In [4]:
def time_since_start(start_time):
    current_time = time.time()
    elapsed_time = current_time - start_time

    hours = int(elapsed_time // 3600)
    minutes = int((elapsed_time % 3600) // 60)
    seconds = int(elapsed_time % 60)
    milliseconds = int((elapsed_time % 1) * 1000)

    return f"{hours}h {minutes}m {seconds}s {milliseconds}ms"

**HSV -> RGB Conversion**

In [10]:
import Images_HSVRGB as HSVRGB
HSVRGB.initializePackages(torch, np, colorsys, go, pio)
trainSet, testSet = HSVRGB.generateTrainAndTestSet(50000, 10000)

In [6]:
# import sys
# sys.path.append('/content')  # Add the directory containing Images_HSVRGB.py to the system path

# from Images_HSVRGB import createTrainAndTestSet  # Import the function from the module

# # Call the function with appropriate arguments
# trainSetLength = 50000  # Example value
# testSetLength = 10000  # Example value
# trainSetHSVRGB, testSetHSVRGB, samplesCube = createTrainAndTestSet(trainSetLength, testSetLength)

# # Now you can use trainSetHSVRGB, testSetHSVRGB, and fig in your notebook

# print(dir(HSVRGB))
# print(len(trainSetHSVRGB), trainSetHSVRGB.dtype)
# print(len(testSetHSVRGB), testSetHSVRGB.dtype)
# display(samplesCube)

In [7]:
small1x1 = []

def createUniqueCalculation(createdCalculations, xMin = 0, xMax = 9, yMin = 0, yMax = 9):
    x = random.randint(xMin, xMax)
    y = random.randint(yMin, yMax)
    while (x, y) in createdCalculations:
        x = random.randint(xMin, xMax)
        y = random.randint(yMin, yMax)
    createdCalculations.append((x, y))
    return x, y

def createSmall1x1():
    global small1x1
    createdCalculations = []
    small1x1 = []

    for trainExample in range(100):
        x, y = createUniqueCalculation(createdCalculations, 0, 9, 0, 9)
        small1x1.append((x, y, x*y, lorem.sentence() + f"{x}*{y}={x*y}"))

In [8]:
datasets = {
    "MNIST": (trainSetMNIST, testSetMNIST),
    "HSV-RGB": (trainSetHSVRGB, testSetHSVRGB),
    #"Cifar10": (trainSetCIFAR10, testSetCIFAR10),
    "Small 1x1": (trainSetCIFAR10, testSetCIFAR10) # Not correct, but doesn´t change anything important
}

NameError: name 'trainSetMNIST' is not defined

In [ ]:
import ipywidgets as widgets
from IPython.display import display, clear_output

def createIntSlider(value, max, description, step=1, min=1, disabled=False):
    slider = widgets.IntSlider(
    value=value,
    min=min,
    max=max,
    step=step,
    description=description,
    disabled=disabled,
    orientation='horizontal',
    readout=True,
    readout_format='d',
    continuous_update=False,
    layout=widgets.Layout(width='95%'),
    style = {'description_width': 'initial'}
    )
    return slider

def createSelectionSlider(value, options, description):
    slider = widgets.SelectionSlider(
        options=options,
        value=value,
        description=description,
        disabled=False,
        continuous_update=False,
        orientation='horizontal',
        readout=True,
        layout=widgets.Layout(width='95%'),
        style = {'description_width': 'initial'}
    )
    return slider

def createLayerChoice(options, tooltips=[], description="Type"):
    layerChoice = widgets.ToggleButtons(
        options=options,
        description=description,
        disabled=False,
        tooltips=tooltips,
        style = {'description_width': 'initial'}
    )
    return layerChoice

def createRangeSliderChoice(max, description):
    options = [f"{i}" for i in range(max)]
    slider = widgets.SelectionRangeSlider(
        options=options,
        index=(0, (max-1)),
        description=description,
        disabled=False,
        layout=widgets.Layout(width='70%'),
        style = {'description_width': 'initial'}
    )
    return slider


def createBoolButtonChoice(description, tooltip, value = False, disabled=False, icon='check'):
    boolButton = widgets.ToggleButton(
        value=value,
        description=description,
        disabled=disabled,
        button_style='', # 'success', 'info', 'warning', 'danger' or ''
        tooltip=tooltip,
        #layout=widgets.Layout(width='20%'),
        style = {'description_width': 'initial'},
        layout=widgets.Layout(width='20%', margin='0% 0% 0% 5%')
        #icon='check' # (FontAwesome names without the `fa-` prefix)
    )
    return boolButton

In [ ]:
datasetChoice = createLayerChoice(options=['MNIST', 'HSV-RGB', 'Cifar10', 'Small 1x1'],
        tooltips=['60000 Written numbers from 0 to 9 (Classification)', '50000 HSV-values (Conversion to RGB)',
                  #'50000 images from 10 classes (Classification)',
                  '90 random values of the small 1x1 (Calculation)'], description='Dataset')

def updateDatasetTab():
    global datasetChoice

    return widgets.VBox([datasetChoice])

In [ ]:
num_layers = 2
layerAmountChoice = createIntSlider(num_layers, min=1, max=16, description="Layer")
seeds = ["Random"] + [i for i in range(100000)]
seedChoice = createSelectionSlider(value="Random", options=seeds, description="Seed")
normalLayerSizeChoice = [createIntSlider(value=128, min=1, max=1024, description="Size", step=1)
       for _ in range(num_layers)]
normalLayerChoice = [createLayerChoice(options=['Linear', 'Conv.2D'],
    tooltips=['Used ideally for ...', 'Used also ideally for ...'], description='Type') for _ in range(num_layers)]
outputLayerChoice = createLayerChoice(options=['Linear', 'Conv.2D'], tooltips=['Used ideally for ...', 'Used also ideally for ...'], description='Type')
activationLayerChoice = [createLayerChoice(options=['ReLU', 'Sigmoid', 'Tanh', 'None'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...', 'Used also especially for ...'],
        description='Type') for _ in range(num_layers)]
outputActivationLayerChoice = createLayerChoice(options=['None', 'ReLU', 'Sigmoid', 'Tanh'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...', 'Used also especially for ...'],
        description='Type', )

# Function to update tab children based on the number of layers
def updateNetworkTab():
    global normalLayerChoice
    global normalLayerSizeChoice
    global activationLayerChoice
    global datasetChoice

    num_layers = layerAmountChoice.value

    if(datasetChoice.value == "Small 1x1"):
        num_layers = 12

    # Create list of ToggleButtons for normal and activation choices for each layer
    normalLayerChoice = [createLayerChoice(options=['Linear', 'Conv.2D'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...'], description='Type') for _ in range(num_layers)]

    normalLayerSizeChoice = [createIntSlider(value=128, min=1, max=1024, description="Size", step=1)
       for _ in range(num_layers)]

    conv2dLayerInputSizeChoice = [createIntSlider(value=128, min=1, max=1024, description="Input Size", step=1)
       for _ in range(num_layers)]
    conv2dLayerOutputSizeChoice = [createIntSlider(value=128, min=1, max=1024, description="Output Size", step=1)
       for _ in range(num_layers)]
    kernelSizeChoice = [createIntSlider(value=3, min=1, max=7, description="Kernel Size", step=1)
       for _ in range(num_layers)]

    activationLayerChoice = [createLayerChoice(options=['ReLU', 'Sigmoid', 'Tanh', 'None'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...', 'Used also especially for ...'],
        description='Type') for _ in range(num_layers)]

    # Create a VBox for each layer with normal and activation choices
    normalLayerVBox = [widgets.VBox([normalLayerChoice[i], normalLayerSizeChoice[i]]) for i in range(num_layers)]
    activationLayerVBox = [widgets.VBox([activationLayerChoice[i]]) for i in range(num_layers)]
    outputLayerVBox = widgets.VBox([outputLayerChoice])
    outputActivationLayerVBox = widgets.VBox([outputActivationLayerChoice])

    # Create list of Accordions for normal and activation layers
    accordionNormalLayer = [widgets.Accordion(children=[normalLayerVBox[i]]) for i in range(num_layers)]
    accordionActivationLayer = [widgets.Accordion(children=[activationLayerVBox[i]]) for i in range(num_layers)]
    accordionOutputLayer = widgets.Accordion(children=[outputLayerVBox])
    accordionOutputActivationLayer = widgets.Accordion(children=[outputActivationLayerVBox])

    tab_nest = widgets.Tab()
    tab_nest.children = [widgets.VBox([accordionNormalLayer[i], accordionActivationLayer[i]]) for i in range(num_layers)] + [widgets.VBox([accordionOutputLayer, accordionOutputActivationLayer])]

    # Set titles for the Accordions
    for i in range(num_layers+1):
        if(i == num_layers):
            tab_nest.set_title(i, f"Output")
            accordionOutputLayer.set_title(0, f'Output Layer')
            accordionOutputActivationLayer.set_title(0, f'Activation Layer')
        else:
            accordionNormalLayer[i].set_title(0, f'Normal Layer')
            accordionActivationLayer[i].set_title(0, f'Activation Layer')
            #chosenLayers.append((accordionNormalLayer[i].children[0].children[1].value, accordionActivationLayer[i].children[0].children[0].value))
            tab_nest.set_title(i, f"Layer {i}")

    if(datasetChoice.value == "Small 1x1"):
        return widgets.VBox([seedChoice, layerAmountChoice])
    else:
        return widgets.VBox([seedChoice, layerAmountChoice, tab_nest])

In [ ]:
trainDataSet = trainSetMNIST
testDataSet = testSetMNIST
maxTrain = len(trainDataSet[0])
maxTest = len(testDataSet[0])
epochsChoice = createIntSlider(10, min=1, max=1000, description="Epochs")
learningRateChoice = widgets.BoundedFloatText(value=0.001, min=0.0000001, max=10.0, step=0.0000001, description='Learning Rate', style = {'description_width': 'initial'}, disabled=False)
trainSamplesChoice = createIntSlider(10000, min=1, max=maxTrain, description="Train Samples")
testSamplesChoice = createIntSlider(2000, min=1, max=maxTest, description="Test Samples")
batchSizeTraining = createIntSlider(64, min=1, max=maxTrain, description="Batchsize Training")
batchSizeTest = createIntSlider(64, min=1, max=maxTest, description="Batchsize Test")
trainingsLink = widgets.jslink((trainSamplesChoice, 'value'), (batchSizeTraining, 'max'))
testLink = widgets.jslink((testSamplesChoice, 'value'), (batchSizeTest, 'max'))
lossChoice = createLayerChoice(options=['MSE', 'Cross-Entropy'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...'], description='Loss-Type')
optimizerChoice = createLayerChoice(options=['Adam', 'SGD'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...'], description='Optimizer-Type')

def updateTrainingTab():
    global trainSamplesChoice
    global testSamplesChoice
    global trainDataSet
    global testDataSet
    global batchSizeTraining
    global batchSizeTest

    maxTrain = len(trainDataSet)
    maxTest = len(testDataSet)
    if(datasetChoice.value == "MNIST"):
        maxTrain = len(trainDataSet[0])
        maxTest = len(testDataSet[0])
    elif(datasetChoice.value == "Small 1x1"):
        maxTrain = 80
        maxTest = 10

    trainSamplesChoice = createIntSlider(10000, min=1, max=maxTrain, description="Train Samples")
    testSamplesChoice = createIntSlider(2000, min=1, max=maxTest, description="Test Samples")
    batchSizeTraining = createIntSlider(64, min=1, max=maxTrain, description="Batchsize Training")
    batchSizeTest = createIntSlider(64, min=1, max=maxTest, description="Batchsize Test")
    trainingsLink = widgets.jslink((trainSamplesChoice, 'value'), (batchSizeTraining, 'max'))
    testLink = widgets.jslink((testSamplesChoice, 'value'), (batchSizeTest, 'max'))

    if(datasetChoice.value == "Small 1x1"):
        #trainTestLink = widgets.jslink((trainSamplesChoice, 'value'), (testSamplesChoice, 'max'))
        return widgets.VBox([epochsChoice, learningRateChoice, trainSamplesChoice, testSamplesChoice])
    else:
        return widgets.VBox([epochsChoice, learningRateChoice, trainSamplesChoice, testSamplesChoice, batchSizeTraining,
            batchSizeTest, lossChoice, optimizerChoice])

In [ ]:
visualizationChoice = createLayerChoice(options=['Weighted', 'Per Neuron & Layer', 'Per Neuron Only', 'Per Layer Only', 'Custom'],
        tooltips=['Used ideally for ...', 'Used also ideally for ...', 'Used also ideally for ...'], description='Visualize')
neuronChoice = [createRangeSliderChoice(max=1024, description=f"Layer {i}") for i in range(num_layers)]
activationLayerTypeChoice = [createBoolButtonChoice(description="ReLU", tooltip="Include activation layer") for i in range(num_layers)]
outputLayerSizeChoice=createRangeSliderChoice(max=10, description=f"Output Layer")
outputLayerActivationChoiceType=createBoolButtonChoice(description=f"Activation layer (ReLU)", tooltip="Include activation layer", disabled = True if outputActivationLayerChoice.value == "None" else False)
layerChoice = [widgets.HBox([neuronChoice[i], activationLayerTypeChoice[i]]) for i in range(num_layers)] + [widgets.HBox([outputLayerSizeChoice, outputLayerActivationChoiceType])]
customBox = widgets.VBox(children=layerChoice)
evalSamplesChoice = createIntSlider(1, min=1, max=100, description="Evaluations")
closestSourceTestLink = widgets.jslink((testSamplesChoice, 'value'), (evalSamplesChoice, 'max'))
closestSourcesChoice = createIntSlider(42, min=1, max=10000, description="Closest Sources")
closestSourceTrainingLink = widgets.jslink((trainSamplesChoice, 'value'), (closestSourcesChoice, 'max'))
showClosestMostUsedSourcesChoice = createIntSlider(3, min=1, max=20, description="Show Closest Sources")

def updateVisualizationTab():
    global normalLayerChoice
    global normalLayerSizeChoice
    global activationLayerChoice
    global neuronChoice
    global activationLayerTypeChoice
    global outputLayerSizeChoice
    global outputLayerActivationChoiceType
    global closestSourcesChoice
    global trainSamplesChoice
    global testSamplesChoice
    global evalSamplesChoice

    outputLayerSizeChoice = createRangeSliderChoice(max=10, description=f"Output Layer")
    outputLayerActivationChoiceType = createBoolButtonChoice(description=f"Activation layer ({outputActivationLayerChoice.value})", tooltip="Include activation layer", disabled = True if outputActivationLayerChoice.value == "None" else False)
    if(datasetChoice.value == "Small 1x1"):
        evalSamplesChoice = createIntSlider(1, min=1, max=100 - trainSamplesChoice.value - testSamplesChoice.value, description="Evaluations")
        closestSourceTrainingLink = widgets.jslink((trainSamplesChoice, 'value'), (closestSourcesChoice, 'max'))
        return widgets.VBox([evalSamplesChoice, closestSourcesChoice, showClosestMostUsedSourcesChoice])

    if(visualizationChoice.value == "Custom"):
        num_layers = layerAmountChoice.value
        neuronChoice = [createRangeSliderChoice(max=normalLayerSizeChoice[i].value, description=f"Neurons in Layer {i} ({normalLayerChoice[i].value})")
            for i in range(num_layers)]
        activationLayerTypeChoice = [createBoolButtonChoice(description=f"Activation layer ({activationLayerChoice[i].value})",
            tooltip="Click to include activation layer in the output", disabled = True if activationLayerChoice[i].value == "None" else False)
            for i in range(num_layers)]
        layerChoice = [widgets.HBox([neuronChoice[i], activationLayerTypeChoice[i]]) for i in range(num_layers)] + [widgets.HBox([outputLayerSizeChoice, outputLayerActivationChoiceType])]
        customBox = widgets.VBox(children=layerChoice)
        closestSourceTrainingLink = widgets.jslink((trainSamplesChoice, 'value'), (closestSourcesChoice, 'max'))
        closestSourceTestLink = widgets.jslink((testSamplesChoice, 'value'), (evalSamplesChoice, 'max'))
        return widgets.VBox([evalSamplesChoice, closestSourcesChoice, showClosestMostUsedSourcesChoice, visualizationChoice, customBox])
    else:
        closestSourceTrainingLink = widgets.jslink((trainSamplesChoice, 'value'), (closestSourcesChoice, 'max'))
        closestSourceTestLink = widgets.jslink((testSamplesChoice, 'value'), (evalSamplesChoice, 'max'))
        return widgets.VBox([evalSamplesChoice, closestSourcesChoice, showClosestMostUsedSourcesChoice, visualizationChoice])

#Initialization

In [ ]:
# @title Click `Show code` in the code cell. { display-mode: "form" }
tab_nest = widgets.Tab()
datasetTab = updateDatasetTab()
networkTab = updateNetworkTab()
trainingTab = updateTrainingTab()
visualizationTab = updateVisualizationTab()

def changeTab(change):
    if change['name'] == 'selected_index' and change['new'] == 3:
        updateChoiceTabs(3)

def observeTabChange():
    if hasattr(observeTabChange, 'tab_observer'):
        tab_nest.unobserve(observeTabChange.tab_observer)
    observeTabChange.tab_observer = tab_nest.observe(changeTab, names='selected_index')

observeTabChange()

def updateChoiceTabs(index, jumpToIndex = True):
    global tab_nest
    global datasetTab
    global networkTab
    global trainingTab
    global visualizationTab

    clear_output()
    tab_nest = widgets.Tab()

    if(index == 0):
        datasetTab = updateDatasetTab()
    elif(index == 1):
        networkTab = updateNetworkTab()
        visualizationTab = updateVisualizationTab()
    elif(index == 2):
        trainingTab = updateTrainingTab()
    elif(index == 3):
        visualizationTab = updateVisualizationTab()

    tab_nest.children = [datasetTab, networkTab, trainingTab, visualizationTab]

    tabNames = ("Datasamples", "Network", "Training", "Visualization")
    for i, name in enumerate(tabNames):
        tab_nest.set_title(i, name)

    if jumpToIndex == True:
        tab_nest.selected_index = index
    tab_nest.unobserve(observeTabChange.tab_observer)
    tab_nest.observe(changeTab, names='selected_index')

    display(tab_nest)

def changeNetworkTab(change):
    updateChoiceTabs(1)

def changeTrainingTab(change):
    global trainDataSet
    global testDataSet

    trainDataSet, testDataSet = datasets[datasetChoice.value]
    updateChoiceTabs(2, jumpToIndex=False)
    updateChoiceTabs(1, jumpToIndex=False)
    updateChoiceTabs(3, jumpToIndex=False)

def changeVisualizationTab(change):
    updateChoiceTabs(3)

# Display the initial widgets
updateChoiceTabs(0)

# Observe all necessary values
layerAmountChoice.observe(changeNetworkTab, names='value')
visualizationChoice.observe(changeVisualizationTab, names='value')
datasetChoice.observe(changeTrainingTab, names='value')

In [ ]:
GPT_CONFIG_124M = {
    "vocab_size": 50257,   # Vocabulary size
    "context_length": 256, # Shortened context length (orig: 1024)
    "emb_dim": 768,        # Embedding dimension
    "n_heads": layerAmountChoice.value,         # Number of attention heads
    "n_layers": layerAmountChoice.value,        # Number of layers
    "drop_rate": 0.1,      # Dropout rate
    "qkv_bias": False      # Query-key-value bias
}

settings = {"learning_rate": learningRateChoice.value, "weight_decay": 0.1, "batch_size": 1, "num_epochs": epochsChoice.value}

In [ ]:
LLM_Layers = [[('Embedding', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["vocab_size"]),
 ('Embedding', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"])],
 #('Dropout', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["drop_rate"])],
  [('LayerNorm', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 ('Linear', GPT_CONFIG_124M["vocab_size"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["vocab_size"])]]

TransformerBlockLayer = [('LayerNorm', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 ('Linear', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 ('Linear', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 ('Linear', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 #('Dropout', 2, GPT_CONFIG_124M["drop_rate"]),
 ('Linear', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"]),
 ('MultiHeadAttention', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["emb_dim"])]
 #('Dropout', GPT_CONFIG_124M["emb_dim"], GPT_CONFIG_124M["drop_rate"])]

In [ ]:
# @title Click `Show code` in the code cell. { display-mode: "form" }
if (seedChoice.value != "Random"):
    torch.manual_seed(seedChoice.value)
    np.random.seed(seedChoice.value)

if(datasetChoice.value == "Small 1x1"):

    hidden_sizes = []
    hidden_sizes.append(LLM_Layers[0])
    for _ in range(layerAmountChoice.value):
        hidden_sizes.append(TransformerBlockLayer)
    hidden_sizes.append(LLM_Layers[1])
    hidden_sizes = [item for sublist in hidden_sizes for item in sublist]

else:
    hidden_sizes = [(normalLayer.value, normalLayerSize.value, activationLayer.value) for normalLayer, normalLayerSize, activationLayer in zip(normalLayerChoice, normalLayerSizeChoice, activationLayerChoice)]
    hidden_sizes.append((outputLayerChoice.value, 10, outputActivationLayerChoice.value))

visualizeCustom = [((normalLayer.value[0], normalLayer.value[1]), activationLayer.value) for normalLayer, activationLayer in zip(neuronChoice, activationLayerTypeChoice)]
visualizeCustom.append(((outputLayerSizeChoice.value[0], outputLayerSizeChoice.value[1]), outputLayerActivationChoiceType.value))

epochs = epochsChoice.value
learning_rate = learningRateChoice.value
train_samples = trainSamplesChoice.value
test_samples = testSamplesChoice.value
batch_size_training = batchSizeTraining.value
batch_size_test = batchSizeTest.value
loss_function = lossChoice.value
optimizer = optimizerChoice.value

eval_samples = evalSamplesChoice.value
closestSources = closestSourcesChoice.value
showClosestMostUsedSources = showClosestMostUsedSourcesChoice.value

if(datasetChoice.value == "Small 1x1"):
    createSmall1x1()
else:
    trainDataSet, testDataSet = datasets[datasetChoice.value]
    x_train, y_train = trainDataSet[0][:train_samples], trainDataSet[1][:train_samples]
    x_test, y_test = testDataSet[0][:test_samples], testDataSet[1][:test_samples]
    x_eval, y_eval = x_test[:eval_samples], y_test[:eval_samples]

#Data Initialization

In [ ]:
class CustomMNISTData(Dataset):
    def __init__(self, mode="", transform = None):
        if mode=="Train":
            self.input = x_train
            self.output = y_train
        elif mode=="Test":
            self.input = x_test
            self.output = y_test
        elif mode=="Evaluate":
            self.input = x_eval
            self.output = y_eval

        self.transform = transform

    def __len__(self):
        return len(self.input)

    def __getitem__(self, idx):
        image = self.input[idx]
        output = self.output[idx]

        return torch.flatten(image), output #array

    def getValues(self, ind):
        array = np.empty([len(ind), 2, 3])
        for x in range(len(ind)):
            array[x] = self.data[ind[x]]

        return array

In [ ]:
class GPTDatasetV1(Dataset):
    def __init__(self, txt, tokenizer, max_length, stride):
        self.input_ids = []
        self.target_ids = []

        # Tokenize the entire text
        token_ids = tokenizer.encode(txt)

        # Use a sliding window to chunk the book into overlapping sequences of max_length
        for i in range(0, len(token_ids) - max_length, stride):
            input_chunk = token_ids[i:i + max_length]
            target_chunk = token_ids[i + 1: i + max_length + 1]
            self.input_ids.append(torch.tensor(input_chunk))
            self.target_ids.append(torch.tensor(target_chunk))

    def __len__(self):
        return len(self.input_ids)

    def __getitem__(self, idx):
        return self.input_ids[idx], self.target_ids[idx]

In [ ]:
if not (datasetChoice.value == "Small 1x1"):
    train_data = CustomMNISTData(mode="Train")
    test_data = CustomMNISTData(mode="Test")
    eval_data = CustomMNISTData(mode="Evaluate")

    train_dataloader = DataLoader(train_data, batch_size=64, shuffle=False)
    test_dataloader = DataLoader(test_data, batch_size=64, shuffle=False)
    eval_dataloader = DataLoader(eval_data, batch_size=1, shuffle=False)

In [ ]:
def create_dataloader_v1(txt, batch_size=4, max_length=256,
                         stride=128, shuffle=True, drop_last=True, num_workers=0):
    # Initialize the tokenizer
    tokenizer = tiktoken.get_encoding("gpt2")

    # Create dataset
    dataset = GPTDatasetV1(txt, tokenizer, max_length, stride)

    # Create dataloader
    dataloader = DataLoader(
        dataset, batch_size=batch_size, shuffle=shuffle, drop_last=drop_last, num_workers=0)

    return dataloader

In [ ]:
def createLLMLoaders():
    actualSamples = [sample[-1] for sample in small1x1]
    samples = "\n".join(actualSamples[:train_samples])

    train_loader = create_dataloader_v1(
        samples,
        batch_size=settings["batch_size"],
        max_length=1,
        stride=1,
        drop_last=False,
        shuffle=False,
        num_workers=0
    )

    samples = "\n".join(actualSamples[train_samples:train_samples+test_samples])
    val_loader = create_dataloader_v1(
        samples,
        batch_size=settings["batch_size"],
        max_length=1,
        stride=1,
        drop_last=False,
        shuffle=False,
        num_workers=0
    )

    samples = "\n".join(actualSamples[train_samples+test_samples:train_samples+test_samples+eval_samples])
    eval_loader = create_dataloader_v1(
        samples,
        batch_size=settings["batch_size"],
        max_length=1,
        stride=1,
        drop_last=False,
        shuffle=False,
        num_workers=0
    )

    return train_loader, val_loader, eval_loader

# Setup Customizable Network

In [ ]:
def getLayer(hidden_layers, layer, input_size=10, output_size=10):
    if(hidden_layers[layer][0] == "Linear"):
        return nn.Linear(input_size, output_size)
    elif(hidden_layers[layer][0] == "Conv2d"):
        return nn.Conv2d(input_size, output_size)
    return False

def getActivation(hidden_layers, layer):
    if(hidden_layers[layer][2] == "ReLU"):
        return nn.ReLU()
    elif(hidden_layers[layer][2] == "Sigmoid"):
        return nn.Sigmoid()
    elif(hidden_layers[layer][2] == "Tanh"):
        return nn.Tanh()
    return False

def checkIfActivationLayerExists(hidden_layers, layer):
    if hidden_layers[layer][2] != "None":
        return True
    return False

layers = []
currentLayer = 0
relevantLayerIndices = []
def createLayers(layerName, layerType, activationLayerType):
    global currentLayer

    layers.append((layerName, layerType, activationLayerType))
    relevantLayerIndices.append(currentLayer*2)
    if(activationLayerType != "None"):
        relevantLayerIndices.append((currentLayer*2)+1)
    currentLayer += 1
    return layerName, layerType

class CustomizableRENN(nn.Module):
    def __init__(self, input_size, hidden_layers, output_size):
        super(CustomizableRENN, self).__init__()
        #Add input and output layer to the hidden_layers
        self.num_layers = (len(hidden_sizes))
        self.hidden_layers = hidden_layers

        for layer in range(self.num_layers):
            if layer == 0:
                setattr(self, *createLayers(f'fc{layer}', getLayer(self.hidden_layers, layer, input_size, hidden_layers[layer][1]), self.hidden_layers[layer][2]))
            elif layer == (self.num_layers - 1):
                setattr(self, *createLayers(f'fc{layer}', getLayer(self.hidden_layers, layer, hidden_layers[layer-1][1], output_size), self.hidden_layers[layer][2]))
            else:
                #print(layer, layer-1, self.num_layers, hidden_sizes[layer-1], hidden_sizes[layer])
                setattr(self, *createLayers(f'fc{layer}', getLayer(self.hidden_layers, layer, hidden_layers[layer-1][1], hidden_layers[layer][1]), self.hidden_layers[layer][2]))

            if checkIfActivationLayerExists(self.hidden_layers, layer):
                setattr(self, f'activation{layer}', getActivation(self.hidden_layers, layer))

    def forward(self, x):
        for layer in range(self.num_layers):
            x = getattr(self, f'fc{layer}')(x)

            if (checkIfActivationLayerExists(self.hidden_layers, layer)):
                x = getattr(self, f'activation{layer}')(x)
        return x

In [ ]:
print(hidden_sizes)

In [ ]:
class MultiHeadAttention(nn.Module):
    def __init__(self, d_in, d_out, context_length, dropout, num_heads, qkv_bias=False):
        super().__init__()
        assert d_out % num_heads == 0, "d_out must be divisible by n_heads"

        self.d_out = d_out
        self.num_heads = num_heads
        self.head_dim = d_out // num_heads  # Reduce the projection dim to match desired output dim

        self.W_query = nn.Linear(d_in, d_out, bias=qkv_bias)
        self.W_key = nn.Linear(d_in, d_out, bias=qkv_bias)
        self.W_value = nn.Linear(d_in, d_out, bias=qkv_bias)
        self.out_proj = nn.Linear(d_out, d_out)  # Linear layer to combine head outputs
        self.dropout = nn.Dropout(dropout)
        self.register_buffer('mask', torch.triu(torch.ones(context_length, context_length), diagonal=1))

    def forward(self, x):
        b, num_tokens, d_in = x.shape

        keys = self.W_key(x)  # Shape: (b, num_tokens, d_out)
        queries = self.W_query(x)
        values = self.W_value(x)

        # We implicitly split the matrix by adding a `num_heads` dimension
        # Unroll last dim: (b, num_tokens, d_out) -> (b, num_tokens, num_heads, head_dim)
        keys = keys.view(b, num_tokens, self.num_heads, self.head_dim)
        values = values.view(b, num_tokens, self.num_heads, self.head_dim)
        queries = queries.view(b, num_tokens, self.num_heads, self.head_dim)

        # Transpose: (b, num_tokens, num_heads, head_dim) -> (b, num_heads, num_tokens, head_dim)
        keys = keys.transpose(1, 2)
        queries = queries.transpose(1, 2)
        values = values.transpose(1, 2)

        # Compute scaled dot-product attention (aka self-attention) with a causal mask
        attn_scores = queries @ keys.transpose(2, 3)  # Dot product for each head

        # Original mask truncated to the number of tokens and converted to boolean
        mask_bool = self.mask.bool()[:num_tokens, :num_tokens]

        # Use the mask to fill attention scores
        attn_scores.masked_fill_(mask_bool, -torch.inf)

        attn_weights = torch.softmax(attn_scores / keys.shape[-1]**0.5, dim=-1)
        attn_weights = self.dropout(attn_weights)

        # Shape: (b, num_tokens, num_heads, head_dim)
        context_vec = (attn_weights @ values).transpose(1, 2)

        # Combine heads, where self.d_out = self.num_heads * self.head_dim
        context_vec = context_vec.reshape(b, num_tokens, self.d_out)
        context_vec = self.out_proj(context_vec)  # optional projection

        return context_vec

In [ ]:
class LayerNorm(nn.Module):
    def __init__(self, emb_dim):
        super().__init__()
        self.eps = 1e-5
        self.scale = nn.Parameter(torch.ones(emb_dim))
        self.shift = nn.Parameter(torch.zeros(emb_dim))

    def forward(self, x):
        mean = x.mean(dim=-1, keepdim=True)
        var = x.var(dim=-1, keepdim=True, unbiased=False)
        norm_x = (x - mean) / torch.sqrt(var + self.eps)
        return self.scale * norm_x + self.shift

In [ ]:
class GELU(nn.Module):
    def __init__(self):
        super().__init__()

    def forward(self, x):
        return 0.5 * x * (1 + torch.tanh(
            torch.sqrt(torch.tensor(2.0 / torch.pi)) *
            (x + 0.044715 * torch.pow(x, 3))
        ))

In [ ]:
class FeedForward(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.layers = nn.Sequential(
            nn.Linear(cfg["emb_dim"], 4 * cfg["emb_dim"]),
            GELU(),
            nn.Linear(4 * cfg["emb_dim"], cfg["emb_dim"]),
        )

    def forward(self, x):
        return self.layers(x)

In [ ]:
class TransformerBlock(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.att = MultiHeadAttention(
            d_in=cfg["emb_dim"],
            d_out=cfg["emb_dim"],
            context_length=cfg["context_length"],
            num_heads=cfg["n_heads"],
            dropout=cfg["drop_rate"],
            qkv_bias=cfg["qkv_bias"])
        self.ff = FeedForward(cfg)
        self.norm1 = LayerNorm(cfg["emb_dim"])
        self.norm2 = LayerNorm(cfg["emb_dim"])
        self.drop_resid = nn.Dropout(cfg["drop_rate"])

    def forward(self, x):
        # Shortcut connection for attention block
        shortcut = x
        x = self.norm1(x)
        x = self.att(x)   # Shape [batch_size, num_tokens, emb_size]
        x = self.drop_resid(x)
        x = x + shortcut  # Add the original input back

        # Shortcut connection for feed-forward block
        shortcut = x
        x = self.norm2(x)
        x = self.ff(x)
        x = self.drop_resid(x)
        x = x + shortcut  # Add the original input back

        return x

In [ ]:
class GPTModel(nn.Module):
    def __init__(self, cfg):
        super().__init__()
        self.tok_emb = nn.Embedding(cfg["vocab_size"], cfg["emb_dim"])
        self.pos_emb = nn.Embedding(cfg["context_length"], cfg["emb_dim"])
        self.drop_emb = nn.Dropout(cfg["drop_rate"])

        self.trf_blocks = nn.Sequential(
            *[TransformerBlock(cfg) for _ in range(cfg["n_layers"])])

        self.final_norm = LayerNorm(cfg["emb_dim"])
        self.out_head = nn.Linear(cfg["emb_dim"], cfg["vocab_size"], bias=False)

    def forward(self, in_idx):
        batch_size, seq_len = in_idx.shape
        in_idx.to(device)
        tok_embeds = self.tok_emb(in_idx)
        pos_embeds = self.pos_emb(torch.arange(seq_len, device=in_idx.device))
        x = tok_embeds + pos_embeds  # Shape [batch_size, num_tokens, emb_size]
        x = self.drop_emb(x)
        x = self.trf_blocks(x)
        x = self.final_norm(x)
        logits = self.out_head(x)
        return logits

In [ ]:
# All necessary variables for training
input_size = len(train_data[0][0])
output_size = len(train_data[0][1])

if (datasetChoice.value == "Small 1x1"):
    model = GPTModel(GPT_CONFIG_124M)
    layers = hidden_sizes
else:
    model = CustomizableRENN(input_size, hidden_sizes, output_size)
    layers = np.array(layers)
model.to(device)

if(loss_function == "MSE"):
    criterion_class = nn.MSELoss()  # For regression
elif(loss_function == "Cross-Entropy"):
    criterion_class = nn.CrossEntropyLoss()  # For multi-class classification

if(optimizer == "Adam"):
    chosen_optimizer = optim.Adam(model.parameters(), lr=learning_rate)
elif(optimizer == "SGD"):
    chosen_optimizer = optim.SGD(model.parameters(), lr=learning_rate)

# Training Customizable RENN

In [ ]:
# Training Loop
def train_model(model, criterion_class,  optimizer, train_dataloader, test_dataloader, epochs=10):
    for epoch in range(epochs):
        model.train()
        train_loss = 0.0
        for images, classification in train_dataloader:
            images = images.to(device)
            classification = classification.to(device)
            optimizer.zero_grad()
            output = model(images)
            loss = criterion_class(output, classification)
            loss.backward()
            optimizer.step()
            train_loss += loss.item()

        # Validation loop
        model.eval()
        val_loss = 0.0
        with torch.no_grad():
            for images, classification in test_dataloader:
                images = images.to(device)
                classification = classification.to(device)
                output = model(images)
                loss = criterion_class(output, classification)
                val_loss += loss.item()

        # Print statistics
        print(f'Epoch {epoch+1}, Train Loss: {train_loss/len(train_dataloader)}, Validation Loss: {val_loss/len(test_dataloader)}')

In [ ]:
def text_to_token_ids(text, tokenizer):
    encoded = tokenizer.encode(text)
    encoded_tensor = torch.tensor(encoded).unsqueeze(0)  # add batch dimension
    return encoded_tensor


def token_ids_to_text(token_ids, tokenizer):
    flat = token_ids.squeeze(0)  # remove batch dimension
    return tokenizer.decode(flat.tolist())

In [ ]:
def calc_loss_batch(input_batch, target_batch, model, device):
    input_batch, target_batch = input_batch.to(device), target_batch.to(device)
    logits = model(input_batch)
    loss = torch.nn.functional.cross_entropy(logits.flatten(0, 1), target_batch.flatten())
    return loss


def calc_loss_loader(data_loader, model, device, num_batches=None):
    total_loss = 0.
    if num_batches is None:
        num_batches = len(data_loader)
    else:
        num_batches = min(num_batches, len(data_loader))
        print("Dataloader: ", num_batches, ", ", len(data_loader))
    for i, (input_batch, target_batch) in enumerate(data_loader):
        if i < num_batches:
            loss = calc_loss_batch(input_batch, target_batch, model, device)
            total_loss += loss.item()
        else:
            break
    return total_loss / num_batches

In [ ]:
def train_model_simple(model, train_loader, val_loader, optimizer, device, num_epochs,
                       eval_freq, eval_iter, start_context, tokenizer):
    # Initialize lists to track losses and tokens seen
    train_losses, val_losses, track_tokens_seen = [], [], []
    tokens_seen = 0
    global_step = -1

    # Main training loop
    for epoch in range(num_epochs):
        model.train()  # Set model to training mode

        for input_batch, target_batch in train_loader:
            optimizer.zero_grad()  # Reset loss gradients from previous epoch
            loss = calc_loss_batch(input_batch, target_batch, model, device)
            loss.backward()  # Calculate loss gradients
            optimizer.step()  # Update model weights using loss gradients
            tokens_seen += input_batch.numel()
            global_step += 1

            # Optional evaluation step
            #if global_step % eval_freq == 0:
        model.eval()
        with torch.no_grad():
            train_loss, val_loss = evaluate_model(
                model, train_loader, val_loader, device, eval_iter)
            train_losses.append(train_loss)
            val_losses.append(val_loss)
            track_tokens_seen.append(tokens_seen)
        #print(f"Ep {epoch+1} (Step {global_step:06d}): "f"Train loss {train_loss:.3f}, Val loss {val_loss:.3f}")
        print(f"Ep {epoch+1}: "f"Train loss {train_loss}, Val loss {val_loss}")


    return train_losses, val_losses, track_tokens_seen

In [ ]:
def evaluate_model(model, train_loader, val_loader, device, eval_iter):
    model.eval()
    with torch.no_grad():
        train_loss = calc_loss_loader(train_loader, model, device, num_batches=eval_iter)
        val_loss = calc_loss_loader(val_loader, model, device, num_batches=eval_iter)
    model.train()
    return train_loss, val_loss

In [ ]:
def plot_losses(epochs_seen, tokens_seen, train_losses, val_losses):
    fig, ax1 = plt.subplots()

    # Plot training and validation loss against epochs
    ax1.plot(epochs_seen, train_losses, label="Training loss")
    ax1.plot(epochs_seen, val_losses, linestyle="-.", label="Validation loss")
    ax1.set_xlabel("Epochs")
    ax1.set_ylabel("Loss")
    ax1.legend(loc="upper right")

    # Create a second x-axis for tokens seen
    ax2 = ax1.twiny()  # Create a second x-axis that shares the same y-axis
    ax2.plot(tokens_seen, train_losses, alpha=0)  # Invisible plot for aligning ticks
    ax2.set_xlabel("Tokens seen")

    fig.tight_layout()  # Adjust layout to make room
    # plt.show()

In [ ]:
def main(model, settings):
    optimizer = torch.optim.AdamW(
        model.parameters(), lr=settings["learning_rate"], weight_decay=settings["weight_decay"]
    )

    tokenizer = tiktoken.get_encoding("gpt2")

    train_loader, val_loader, eval_loader = createLLMLoaders()

    train_losses, val_losses, tokens_seen = train_model_simple(
        model, train_loader, val_loader, optimizer, device,
        num_epochs=settings["num_epochs"], eval_freq=5, eval_iter=1,
        start_context="=", tokenizer=tokenizer
    )

    return train_losses, val_losses, tokens_seen, train_loader, eval_loader, model

In [ ]:
# Train the model
trainTime = time.time()
if (datasetChoice.value == "Small 1x1"):
    _, _, _, train_dataloader, eval_dataloader, model = main(model, settings)
    tokenizer = tiktoken.get_encoding("gpt2")
else:
    train_model(model, criterion_class, chosen_optimizer, train_dataloader, test_dataloader, epochs=epochs)
print(f"Time passed since start of training: {time_since_start(trainTime)}")

# Sourcecheck Customisable RENN

In [ ]:
layerSizes = [size[1] for size in hidden_sizes[:]]
totalLayers = len(layers)*2
if (datasetChoice.value == "Small 1x1"): totalLayers = len(layers)
activationsBySources = np.full((train_samples, totalLayers, np.max(layerSizes)), 100000)
activationsByLayers = np.full((totalLayers, np.max(layerSizes), train_samples), 100000)
print(activationsBySources.shape)
print(activationsByLayers.shape)

In [ ]:
#Variables for usage within the hook
layer = 0
source = 0
dictionaryForSourceLayerNeuron = activationsBySources
dictionaryForLayerNeuronSource = activationsByLayers
if not (datasetChoice.value == "Small 1x1"):
    train_dataloader = DataLoader(train_data, batch_size=1, shuffle=False)
print(layers)

# Forward hook
def forward_hook(module, input, output):
    global layer
    global source
    global dictionaryForSourceLayerNeuron
    global dictionaryForLayerNeuronSource
    global hidden_sizes
    global datasetChoice

    if not (isinstance(module, nn.Sequential) or isinstance(module, FeedForward) or isinstance(module, TransformerBlock) or isinstance(module, nn.Dropout)):
        if (datasetChoice.value == "Small 1x1"):
            actualLayer = layer
            layerNeurons = layers[actualLayer][1]
            if(source >= dictionaryForSourceLayerNeuron.shape[0]):
                return
        else:
            actualLayer = int(layer/2)
            layerNeurons = layers[actualLayer][1].out_features

        activation_type = type(getActivation(hidden_sizes, actualLayer))
        layer_type = type(getLayer(hidden_sizes, actualLayer))
        relevantOutput = output[0].cpu().numpy()

        #print(layer, layers[layer], relevantOutput.shape)

        if (type(module) == activation_type or type(module) == layer_type or datasetChoice.value == "Small 1x1"):
            #Use for array structure like: [source, layer, neuron]
            if(len(relevantOutput.shape) > 1):
                if(relevantOutput.shape[1] != layerNeurons):
                    layerNeurons = relevantOutput.shape[1]
                    #layers[actualLayer] = (layers[actualLayer][0], relevantOutput.shape[1], layers[layer][2:])
            dictionaryForSourceLayerNeuron[source][layer,:layerNeurons] = relevantOutput

            #Use for array structure like: [layer, neuron, source]
            # if(datasetChoice.value == "Small 1x1"):
            #     if()
            #     print(actualLayer, relevantOutput.shape, len(relevantOutput.shape))
            #     for neuronNumber in range(layers[actualLayer][1]):
            #         if neuronNumber < layerNeurons:
            #             dictionaryForLayerNeuronSource[actualLayer][neuronNumber][source] = relevantOutput[0][neuronNumber]
            #         else:
            #             break
            # else:
            output = relevantOutput if len(relevantOutput.shape) == 1 else relevantOutput[0]
            for neuronNumber, neuron in enumerate(output):
                if neuronNumber < layerNeurons:
                    dictionaryForLayerNeuronSource[actualLayer][neuronNumber][source] = neuron
                else:
                    break

        if(layer % 2 == 0 and not datasetChoice.value == "Small 1x1"):
            if(checkIfActivationLayerExists(hidden_sizes, actualLayer)):
                layer += 1
            elif(layer == (len(layers)*2)-2):
                layer = 0
            else:
                layer += 2
        else:
            if((layer == (len(layers)*2)-1 and not datasetChoice.value == "Small 1x1") or (layer == (len(layers))-1 and datasetChoice.value == "Small 1x1")):
                layer = 0
            else:
                layer += 1
#-------------------------------------------------------------------------------

def attachHooks(hookLoader, model):
    global source
    layer = 0
    source = 0

    hooks = []  # Store the handles for each hook
    outputs = np.array([])

    for name, module in model.named_modules():
      if not isinstance(module, type(model)):
          hook = module.register_forward_hook(forward_hook)
          hooks.append(hook)

    with torch.no_grad():
      # Forward Pass
      convertTime = time.time()
      for source, (inputs, labels) in enumerate(hookLoader):
        inputs = inputs.to(device)
        _ = model(inputs)

      print(f"Time passed since conversion: {time_since_start(convertTime)}")

    # Remove hooks after use
    for hook in hooks:
        hook.remove()

attachHooks(train_dataloader, model)
activationsBySources = dictionaryForSourceLayerNeuron
activationsByLayers = dictionaryForLayerNeuronSource

In [ ]:
activationsBySources[0][0]

# Visualization Customisable RENN

In [ ]:
import matplotlib.pyplot as plt
from collections import Counter
from PIL import Image

def showImagesUnweighted(originalImage, blendedSourceImageActivation, blendedSourceImageSum, closestMostUsedSourceImagesActivation, closestMostUsedSourceImagesSum):
    fig, axes = plt.subplots(1, 5, figsize=(35, 35))
    plt.subplots_adjust(hspace=0.5)

    # Display original image
    axes[0].set_title(f"BLENDED - Original: {originalImage[1]}")
    axes[0].imshow(Image.fromarray(originalImage[0].cpu().numpy()*255))

    # Display blendedSourceImageActivation
    axes[1].set_title(f"A=Activation - Closest Sources/Neuron (Most Used)")
    axes[1].imshow(blendedSourceImageActivation[0])

    # Display blendedSourceImageSum
    axes[2].set_title(f"S=Sum - Closest Sources/Neuron (Most Used)")
    axes[2].imshow(blendedSourceImageSum[0])

    # Display weightedSourceImageActivation
    axes[3].set_title(f"WA=WeightedActivation - Closest Sources/Neuron (Weighted)")
    axes[3].imshow(Image.fromarray(np.zeros(shape=[28,28], dtype=np.uint8)).convert("RGBA"))

    # Display weightedSourceImageSum
    axes[4].set_title(f"WS=WeigthedSum - Closest Sources/Neuron (Weighted)")
    axes[4].imshow(Image.fromarray(np.zeros(shape=[28,28], dtype=np.uint8)).convert("RGBA"))

    plt.show()

    # Display closestMostUsedSourceImagesActivation
    fig, axes = plt.subplots(1, len(closestMostUsedSourceImagesActivation)+2, figsize=(35, 35))
    axes[0].set_title(f"NON-LINEAR - Original: {originalImage[1]}")
    axes[0].imshow(Image.fromarray(originalImage[0].cpu().numpy()*255))
    axes[1].set_title(f"A - Closest Sources/Neuron (Most Used)")
    axes[1].imshow(blendedSourceImageActivation[0])
    for i, source in enumerate(closestMostUsedSourceImagesActivation):
        image = createImageWithPrediction(x_train[source[0]], y_train[source[0]], predict(x_train[source[0]]))
        axes[i+2].set_title(f"A - Source {source[0]} ({blendedSourceImageActivation[1][i]:.4f}): {image[1]}")
        axes[i+2].imshow(Image.fromarray(image[0].cpu().numpy()*255))
    plt.show()

    # Display closestMostUsedSourceImagesSum
    fig, axes = plt.subplots(1, len(closestMostUsedSourceImagesSum)+2, figsize=(35, 35))
    axes[0].set_title(f"LINEAR - Original: {originalImage[1]}")
    axes[0].imshow(Image.fromarray(originalImage[0].cpu().numpy()*255))
    axes[1].set_title(f"S - Closest Sources/Neuron (Most Used)")
    axes[1].imshow(blendedSourceImageSum[0])
    for i, source in enumerate(closestMostUsedSourceImagesSum):
        image = createImageWithPrediction(x_train[source[0]], y_train[source[0]], predict(x_train[source[0]]))
        axes[i+2].set_title(f"S - Source {source[0]} ({blendedSourceImageSum[1][i]:.4f}x): {image[1]}")
        axes[i+2].imshow(Image.fromarray(image[0].cpu().numpy()*255))
    plt.show()

In [ ]:
import plotly.graph_objects as go
import plotly.subplots as sp

def showIndividualImagesPlotly(images, layer, mode):
    print(len(images))
    num_images = len(images)
    num_cols = 5  # Number of columns
    if num_images == 10:
        num_cols = 5
    num_rows = num_images // num_cols if (num_images // num_cols >= 1) else 1  # Number of rows
    if num_images % num_cols != 0:
        num_rows = num_images // num_cols + 1  # Number of rows

    fig = sp.make_subplots(rows=num_rows, cols=num_cols)

    for i, (image, sources, title) in enumerate(images):
        row_index = i // num_cols
        col_index = i % num_cols
        fig.add_trace(go.Image(name=f'<b>{title}</b><br>Closest {showClosestMostUsedSources} Sources compared by {mode}:<br>{sources}', z=image), row=row_index + 1, col=col_index + 1)

    fig.update_layout(
        title=f'Blended closest {closestSources} sources for each neuron in layer {layer} (compared to their {mode} output)',
        grid={'rows': num_rows, 'columns': num_cols},
        height=225 * num_rows,  # Adjust the height of the plot
        width=225 * num_cols,
        hoverlabel=dict(namelength=-1)
    )

    #fig.show()
    display(fig)

In [ ]:
from dataclasses import dataclass
@dataclass(order=True)
class WeightedSource:
  source: int
  difference: float

In [ ]:
def getMostUsed(sources, mode=""):
    mostUsed = []
    sourceCounter = 0
    for currentLayer, layer in enumerate(sources):
        for currentNeuron, neuron in enumerate(layer):
            maxNeurons = layers[currentLayer][1] if mode=="" else layers[currentLayer][1].out_features
            if(currentNeuron < maxNeurons):
                for sourceNumber, value, difference in neuron:
                    mostUsed.append(sourceNumber)
                    sourceCounter += 1
    return sourceCounter, mostUsed

In [ ]:
def getMostUsedSources(sources, weightedMode=""):
    weightedSources = []

    sourceCounter, mostUsed = getMostUsed(sources, weightedMode)
    counter = Counter(mostUsed)

    print(sourceCounter, counter.most_common())
    return counter.most_common()[:closestSources]

In [ ]:
def getMostUsedPerLayer(sources):
    mostUsed = []
    sourceCounter = 0
    for src in sources:
        mostUsed.append(src.source)
        sourceCounter += 1
    return sourceCounter, mostUsed

In [ ]:
def getClosestSourcesPerNeuronAndLayer(sources, layersToCheck, mode=""):
    for cLayer, layer in enumerate(sources):
        weightedSourcesPerLayer = []
        totalDifferencePerLayer = 0
        imagesPerLayer = []

        for cNeuron, neuron in enumerate(layer):
            if(cNeuron < layers[cLayer][1].out_features):
                weightedSourcesPerNeuron = []
                totalDifferencePerNeuron = 0
                for sourceNumber, value, difference in neuron:
                    baseWeightedSource = {'source': sourceNumber, 'difference': difference}
                    totalDifferencePerNeuron += difference
                    totalDifferencePerLayer += difference
                    weightedSourcesPerNeuron.append(WeightedSource(**baseWeightedSource))
                    weightedSourcesPerLayer.append(WeightedSource(**baseWeightedSource))
                if not(visualizationChoice.value == "Custom" and ((cNeuron < int(visualizeCustom[cLayer][0][0])) or (cNeuron > int(visualizeCustom[cLayer][0][1])))):
                    imagesPerLayer.append([blendIndividualImagesTogether(weightedSourcesPerNeuron), [f"Source: {source.source}, Difference: {source.difference:.10f}<br>" for source in weightedSourcesPerNeuron][:showClosestMostUsedSources], f"{mode} - Layer: {int(layersToCheck[cLayer]/2)}, Neuron: {cNeuron}"])

        if not(visualizationChoice.value == "Per Layer Only"):
            if not(mode == "Activation" and visualizationChoice.value == "Custom" and visualizeCustom[cLayer][1] == False):
                showIndividualImagesPlotly(imagesPerLayer, int(layersToCheck[cLayer]/2), mode)

        if not(visualizationChoice.value == "Per Neuron Only"):
            if not(mode == "Activation" and visualizationChoice.value == "Custom" and visualizeCustom[cLayer][1] == False):
                weightedSourcesPerLayer = sorted(weightedSourcesPerLayer, key=lambda x: x.difference)
                sourceCounter, mostUsed = getMostUsedPerLayer(weightedSourcesPerLayer)
                counter = Counter(mostUsed)
                image = blendIndividualImagesTogether(counter.most_common()[:closestSources], True)

                plt.figure(figsize=(28,28))
                plt.imshow(image)
                plt.title(f"{mode} - Layer:  {int(layersToCheck[cLayer]/2)}, {closestSources} most used Sources")
                plt.show()

In [ ]:
def blendIndividualImagesTogether(mostUsedSources, layer=False):
    image = Image.fromarray(np.zeros(shape=[28,28], dtype=np.uint8)).convert("RGBA")

    total = 0
    for source in mostUsedSources:
        if(layer):
            total += source[1]
        else:
            total += source.difference

    for wSource in mostUsedSources:
        #TODO: NORMALIZATION!!!
        if(total > 0):
            if(closestSources < 2):
                if(layer):
                    image = Image.blend(image, Image.fromarray(x_train[wSource[0]].numpy()*255).convert("RGBA"), 1)
                else:
                    image = Image.blend(image, Image.fromarray(x_train[wSource.source].numpy()*255).convert("RGBA"), 1)
            else:
                if(layer):
                    image = Image.blend(image, Image.fromarray(x_train[wSource[0]].numpy()*255).convert("RGBA"), wSource[1] / total)
                else:
                    #print(f"Diff: {wSource.difference}, Total: {total}, Calculation: {(1 - (wSource.difference / total)) / closestSources}")
                    image = Image.blend(image, Image.fromarray(x_train[wSource.source].numpy()*255).convert("RGBA"), (1 - (wSource.difference / total)) / closestSources)

    return image

In [ ]:
def blendImagesTogether(mostUsedSources, mode):
    image = Image.fromarray(np.zeros(shape=[28,28], dtype=np.uint8)).convert("RGBA")
    weights = []
    total = 0

    if mode == "Not Weighted":
        for sourceNumber, counter in mostUsedSources:
            total += counter

        for sourceNumber, counter in mostUsedSources:
            #TODO: NORMALIZATION!!!
            image = Image.blend(image, Image.fromarray(x_train[sourceNumber].numpy()*255).convert("RGBA"), (counter/total))
            weights.append(counter/total)

    return (image, weights)

In [ ]:
def identifyClosestSources(dictionary, outputs, mode = ""):
    if(mode == "Sum"):
        layerNumbersToCheck = [idx*2 for idx, (name, layer, activation) in enumerate(layers)]
    elif(mode == "Activation"):
        layerNumbersToCheck = [(idx*2)+1 for idx, (name, layer, activation) in enumerate(layers) if getActivation(hidden_sizes, idx) != False]
    else:
        layerNumbersToCheck = [idx for idx, _ in enumerate(layers)]

    layersToCheck = dictionary[layerNumbersToCheck]
    outputsToCheck = outputs[layerNumbersToCheck]
    identifiedClosestSources = np.empty((len(layersToCheck), np.max(layerSizes), closestSources), dtype=tuple)

    #print(len(layersToCheck), len(outputsToCheck))
    for currentLayer, layer in enumerate(layersToCheck):
        for currentNeuron, neuron in enumerate(layer):
            maxNeurons = layers[currentLayer][1] if mode=="" else layers[currentLayer][1].out_features
            if(currentNeuron < maxNeurons):
                #print(currentLayer, currentNeuron, len(neuron), outputsToCheck[currentLayer][currentNeuron], outputsToCheck.shape)
                differencesBetweenSources = np.abs(neuron - np.full(len(neuron), outputsToCheck[currentLayer][currentNeuron]))
                sortedSourceIndices = np.argsort(differencesBetweenSources) # for highest difference uncomment this: [::-1]
                closestSourceIndices = sortedSourceIndices[:closestSources]
                tuples = tuple((closestSourceIndices[i], neuron[closestSourceIndices[i]], abs(neuron[closestSourceIndices[i]]-outputsToCheck[currentLayer][currentNeuron])) for i in range(closestSources))
                identifiedClosestSources[currentLayer][currentNeuron] = tuples
    return identifiedClosestSources, outputsToCheck, layerNumbersToCheck

In [ ]:
def predict(sample):
    with torch.no_grad():
        sample = sample.to(device)
        model.eval()
        output = model(torch.flatten(sample))
    normalizedPredictions = normalizePredictions(output.cpu().numpy())
    return np.argmax(normalizedPredictions), normalizedPredictions[np.argmax(normalizedPredictions)]

In [ ]:
def createImageWithPrediction(sample, true, prediction):
    sample = sample.to(device)
    true = true.to(device)
    prediction, probability = predict(sample)
    true_class = int(torch.argmax(true.cpu()))  # Move `true` tensor to CPU and then get the index of the maximum value
    return [sample, f"pred: {prediction}, prob: {probability:.2f}, true: {true_class}"]

In [ ]:
def normalizePredictions(array):
    min = np.min(array)
    max = np.max(array)
    return (array - min) / (max - min)

In [ ]:
def generate(model, idx, max_new_tokens, context_size, temperature, top_k=None):

    # For-loop is the same as before: Get logits, and only focus on last time step
    for _ in range(max_new_tokens):
        idx_cond = idx[:, -context_size:]
        with torch.no_grad():
            logits = model(idx_cond.to(device))
        logits = logits[:, -1, :]

        # New: Filter logits with top_k sampling
        if top_k is not None:
            # Keep only top_k values
            top_logits, _ = torch.topk(logits, top_k)
            min_val = top_logits[:, -1]
            logits = torch.where(logits < min_val, torch.tensor(float('-inf')).to(logits.device), logits)

        # New: Apply temperature scaling
        if temperature > 0.0:
            logits = logits / temperature

            # Apply softmax to get probabilities
            probs = torch.softmax(logits, dim=-1)  # (batch_size, context_len)

            # Sample from the distribution
            idx_next = torch.multinomial(probs, num_samples=1)  # (batch_size, 1)

        # Otherwise same as before: get idx of the vocab entry with the highest logits value
        else:
            idx_next = torch.argmax(logits, dim=-1, keepdim=True)  # (batch_size, 1)

        # Same as before: append sampled index to the running sequence
        idx = torch.cat((idx.to(device), idx_next.to(device)), dim=1)  # (batch_size, num_tokens+1)

    return idx

In [ ]:
def getLLMPrediction(sample):
    x, y, solution, _ = sample
    index = text_to_token_ids(f"{x}*{y}=", tokenizer)
    maxNewTokens = len(str(x*y))
    contextSize = len(str(f"{x}*{y}="))
    token_ids = generate(model=model, idx=index, max_new_tokens=maxNewTokens,
    context_size=contextSize, top_k=1, temperature=1.0)
    prediction = token_ids_to_text(token_ids, tokenizer)
    return x, y, solution, prediction

In [ ]:
#Make sure to set new dictionarys for the hooks to fill - they are global!
dictionaryForSourceLayerNeuron = np.full((eval_samples, totalLayers, np.max(layerSizes)), 100000)
dictionaryForLayerNeuronSource = np.full((totalLayers, np.max(layerSizes), eval_samples), 100000)

with torch.no_grad():
    model.eval()  # Set the model to evaluation mode
    attachHooks(eval_dataloader, model)

if (datasetChoice.value == "Small 1x1"):
    for sampleNumber in range(eval_samples):
        #TODO: Save calculations to file and hook in evaluation mode onto the model!
        sources, outputs, layerNumbersToCheck = identifyClosestSources(activationsByLayers, dictionaryForSourceLayerNeuron[sampleNumber])
        #print(activationsByLayers, dictionaryForSourceLayerNeuron[sampleNumber])
        mostUsedSources = getMostUsedSources(sources, "")
        x, y, solution, prediction = getLLMPrediction(small1x1[train_samples+test_samples+sampleNumber])
        print(prediction, f" -> Difference = {(solution) - (int(prediction) if prediction.isdigit() else 0)}")
        print([(sourceNumber, count, small1x1[sourceNumber][3]) for sourceNumber, count in mostUsedSources])
else:
    for pos, (sample, true) in enumerate(zip(x_eval, y_eval)):
        prediction = predict(sample)

        if(visualizationChoice.value == "Weighted"):
            sourcesSum, outputsSum, layerNumbersToCheck = identifyClosestSources(activationsByLayers, dictionaryForSourceLayerNeuron[pos], "Sum")

            mostUsedSourcesWithSum = getMostUsedSources(sourcesSum, "Sum")
            blendedSourceImageSum = blendImagesTogether(mostUsedSourcesWithSum[:20], "Not Weighted")

            sourcesActivation, outputsActivation, layerNumbersToCheck = identifyClosestSources(activationsByLayers, dictionaryForSourceLayerNeuron[pos], "Activation")
            mostUsedSourcesWithActivation = getMostUsedSources(sourcesActivation, "Activation")
            blendedSourceImageActivation = blendImagesTogether(mostUsedSourcesWithActivation[:20], "Not Weighted")

            showImagesUnweighted(createImageWithPrediction(sample, true, prediction), blendedSourceImageActivation, blendedSourceImageSum, mostUsedSourcesWithActivation[:showClosestMostUsedSources], mostUsedSourcesWithSum[:showClosestMostUsedSources])
        else:
            sourcesSum, outputsSum, layerNumbersToCheck = identifyClosestSources(activationsByLayers, dictionaryForSourceLayerNeuron[pos], "Sum")
            mostUsedSourcesWithSum = getClosestSourcesPerNeuronAndLayer(sourcesSum, layerNumbersToCheck, "Sum")

            sourcesActivation, outputsActivation, layerNumbersToCheck = identifyClosestSources(activationsByLayers, dictionaryForSourceLayerNeuron[pos], "Activation")
            mostUsedSourcesWithActivation = getClosestSourcesPerNeuronAndLayer(sourcesActivation, layerNumbersToCheck, "Activation")

print(f"Time passed since start: {time_since_start(startTime)}")